In [0]:
# pip install pyspark

In [0]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import col, concat_ws, split

In [0]:
SparkSession

pyspark.sql.session.SparkSession

In [0]:
spark = SparkSession.builder.appName('Youtube_Data_Analysis').getOrCreate()

In [0]:
spark

In [0]:
spark.sparkContext

<SparkContext master=spark://10.139.64.4:7077 appName=Databricks Shell>

In [0]:
from pyspark.sql.types import StructType,StructField,StringType,IntegerType
from pyspark.sql.functions import *

In [0]:
# Load the CSV file without headers
# Read the CSV file with space separator
df = spark.read.csv('file:/Workspace/Users/d-user11@heu.ai/youtubedata.csv',header=False,inferSchema=True)
df.toPandas()

_c0                   _c1  ...         _c21         _c22
0     QuRYeRnAuXM  EvilSquirrelPictures  ...  u6_DQQjLsAw  73Wz9CQFDtE
1     3TYqkBJ9YRk                hggh22  ...  I4yKEK9o8gA  zQ83d_D2MGs
2     rSJ8QZWBegU               TimeGem  ...  YZev1imoxX8  I4yKEK9o8gA
3     nRcovJn9xHg            wooochacha  ...  zQ83d_D2MGs  1GKaVzNDbuI
4     UEvVksP91kg              johnx113  ...  I4yKEK9o8gA  zQ83d_D2MGs
...           ...                   ...  ...          ...          ...
4095  esCvu46qDaA                 RSMFD  ...  G8OlUZEnyOA  M80K51DosFo
4096  kOZ8bRAO7YQ         RockstarGames  ...         None         None
4097  GSsVZcKHues               GTASite  ...  q3qdBVDZrmE  hKSk1bW9qzw
4098  foKRqJGcbPQ       scrambledeggsTV  ...  z84ko4Xzn40  Qjj_uMubxP0
4099  -CYhSNHbeC8               rehab07  ...  0n1plrwQwrk  GZ_ct8ad-dY

[4100 rows x 23 columns]

In [0]:
# Define the column names
column_names = [
    "Video ID", 
    "Video Uploader", 
    "Interval between YouTube Establishment and Video Upload",
    "Video Category", 
    "Video Length", 
    "Number of Views", 
    "Rating on the Video", 
    "Number of Ratings", 
    "Number of Comments", 
    "Related Video IDs"
]


# Rename the first 9 columns using the provided names
for i in range(len(column_names)):
    df = df.withColumnRenamed(f"_c{i}", column_names[i])    
    

In [0]:
df.show()

+-----------+--------------------+-------------------------------------------------------+----------------+------------+---------------+-------------------+-----------------+------------------+-----------------+-----------+-----------+-----------+-----------+-----------+-----------+-----------+-----------+-----------+-----------+-----------+-----------+-----------+
|   Video ID|      Video Uploader|Interval between YouTube Establishment and Video Upload|  Video Category|Video Length|Number of Views|Rating on the Video|Number of Ratings|Number of Comments|Related Video IDs|       _c10|       _c11|       _c12|       _c13|       _c14|       _c15|       _c16|       _c17|       _c18|       _c19|       _c20|       _c21|       _c22|
+-----------+--------------------+-------------------------------------------------------+----------------+------------+---------------+-------------------+-----------------+------------------+-----------------+-----------+-----------+-----------+-----------+-----

In [0]:
from pyspark.sql.functions import concat_ws, col

# Columns to combine: from _c10 to _c22
columns_to_combine = [col(f'_c{i}') for i in range(10, 23)]

# Combine all relevant columns into a single column called "Related Video IDs"
df = df.withColumn("Related Video IDs", concat_ws(" ", *columns_to_combine))

# Drop the original _c10 to _c22 columns
columns_to_drop = [f'_c{i}' for i in range(10, 23)]
df = df.drop(*columns_to_drop)

In [0]:

# Show the result
df.show()

+-----------+--------------------+-------------------------------------------------------+----------------+------------+---------------+-------------------+-----------------+------------------+--------------------+
|   Video ID|      Video Uploader|Interval between YouTube Establishment and Video Upload|  Video Category|Video Length|Number of Views|Rating on the Video|Number of Ratings|Number of Comments|   Related Video IDs|
+-----------+--------------------+-------------------------------------------------------+----------------+------------+---------------+-------------------+-----------------+------------------+--------------------+
|QuRYeRnAuXM|EvilSquirrelPictures|                                                 1135.0|  Pets & Animals|         252|           1075|               4.96|               46|                86|nRcovJn9xHg 3TYqk...|
|3TYqkBJ9YRk|              hggh22|                                                 1135.0|          Comedy|         169|            228|    

In [0]:

from pyspark.sql.functions import col, regexp_replace

# Replace spaces with commas in the 'final_column' column
df = df.withColumn('Related Video IDs', regexp_replace(col('Related Video IDs'), ' ', ','))

In [0]:
df.toPandas()

Video ID  ...                                  Related Video IDs
0     QuRYeRnAuXM  ...  nRcovJn9xHg,3TYqkBJ9YRk,rSJ8QZWBegU,0TZqX5MbXM...
1     3TYqkBJ9YRk  ...  gFa1YMEJFag,UEvVksP91kg,rSJ8QZWBegU,nRcovJn9xH...
2     rSJ8QZWBegU  ...  gFa1YMEJFag,UEvVksP91kg,3TYqkBJ9YRk,nRcovJn9xH...
3     nRcovJn9xHg  ...  gFa1YMEJFag,UEvVksP91kg,3TYqkBJ9YRk,ZTopArY7Nb...
4     UEvVksP91kg  ...  QuRYeRnAuXM,3TYqkBJ9YRk,0TZqX5MbXMA,rSJ8QZWBeg...
...           ...  ...                                                ...
4095  esCvu46qDaA  ...  vOskZNJJII8,q3qdBVDZrmE,mLDLe024T_I,bhLbFGVduT...
4096  kOZ8bRAO7YQ  ...                                                   
4097  GSsVZcKHues  ...  vOskZNJJII8,_X5nHLOiAVo,cNION6wGuso,5-reBn0gUk...
4098  foKRqJGcbPQ  ...  _X5nHLOiAVo,5-reBn0gUkg,e8bEzU2Tx7c,e4yx1s-l6f...
4099  -CYhSNHbeC8  ...  EOj-iWkcJPU,pg3j4IBMRZE,2GHiAEeFQs0,e4yx1s-l6f...

[4100 rows x 10 columns]

In [0]:
df.count()

4100

In [0]:
# Drop Null Values 

In [0]:
df_cleaned=df.dropna(how="any")

In [0]:
df_cleaned.count()

4066

In [0]:
df_cleaned.printSchema()

root
 |-- Video ID: string (nullable = true)
 |-- Video Uploader: string (nullable = true)
 |-- Interval between YouTube Establishment and Video Upload: double (nullable = true)
 |-- Video Category: string (nullable = true)
 |-- Video Length: integer (nullable = true)
 |-- Number of Views: integer (nullable = true)
 |-- Rating on the Video: double (nullable = true)
 |-- Number of Ratings: integer (nullable = true)
 |-- Number of Comments: integer (nullable = true)
 |-- Related Video IDs: string (nullable = false)



In [0]:
data=df_cleaned

In [0]:
data.count()

4066

In [0]:
data.toPandas()

Video ID  ...                                  Related Video IDs
0     QuRYeRnAuXM  ...  nRcovJn9xHg,3TYqkBJ9YRk,rSJ8QZWBegU,0TZqX5MbXM...
1     3TYqkBJ9YRk  ...  gFa1YMEJFag,UEvVksP91kg,rSJ8QZWBegU,nRcovJn9xH...
2     rSJ8QZWBegU  ...  gFa1YMEJFag,UEvVksP91kg,3TYqkBJ9YRk,nRcovJn9xH...
3     nRcovJn9xHg  ...  gFa1YMEJFag,UEvVksP91kg,3TYqkBJ9YRk,ZTopArY7Nb...
4     UEvVksP91kg  ...  QuRYeRnAuXM,3TYqkBJ9YRk,0TZqX5MbXMA,rSJ8QZWBeg...
...           ...  ...                                                ...
4061  esCvu46qDaA  ...  vOskZNJJII8,q3qdBVDZrmE,mLDLe024T_I,bhLbFGVduT...
4062  kOZ8bRAO7YQ  ...                                                   
4063  GSsVZcKHues  ...  vOskZNJJII8,_X5nHLOiAVo,cNION6wGuso,5-reBn0gUk...
4064  foKRqJGcbPQ  ...  _X5nHLOiAVo,5-reBn0gUkg,e8bEzU2Tx7c,e4yx1s-l6f...
4065  -CYhSNHbeC8  ...  EOj-iWkcJPU,pg3j4IBMRZE,2GHiAEeFQs0,e4yx1s-l6f...

[4066 rows x 10 columns]

In [0]:
data.describe().toPandas()

summary  ...                                  Related Video IDs
0   count  ...                                               4066
1    mean  ...                                               None
2  stddev  ...                                               None
3     min  ...                                                   
4     max  ...  zzlDKaXAIgE,e_Oun_GTKDo,4ira1eUOQGY,RWS45QqP1l...

[5 rows x 11 columns]

In [0]:
null_count=data.filter(data["Related Video IDs"].isNull()).count()
null_count

0

In [0]:
data.select('Related Video IDs').toPandas()

Related Video IDs
0     nRcovJn9xHg,3TYqkBJ9YRk,rSJ8QZWBegU,0TZqX5MbXM...
1     gFa1YMEJFag,UEvVksP91kg,rSJ8QZWBegU,nRcovJn9xH...
2     gFa1YMEJFag,UEvVksP91kg,3TYqkBJ9YRk,nRcovJn9xH...
3     gFa1YMEJFag,UEvVksP91kg,3TYqkBJ9YRk,ZTopArY7Nb...
4     QuRYeRnAuXM,3TYqkBJ9YRk,0TZqX5MbXMA,rSJ8QZWBeg...
...                                                 ...
4061  vOskZNJJII8,q3qdBVDZrmE,mLDLe024T_I,bhLbFGVduT...
4062                                                   
4063  vOskZNJJII8,_X5nHLOiAVo,cNION6wGuso,5-reBn0gUk...
4064  _X5nHLOiAVo,5-reBn0gUkg,e8bEzU2Tx7c,e4yx1s-l6f...
4065  EOj-iWkcJPU,pg3j4IBMRZE,2GHiAEeFQs0,e4yx1s-l6f...

[4066 rows x 1 columns]

In [0]:
data[data['Related Video IDs']==''].count()

827

In [0]:
# Replace empty strings with null in 'Related Video IDs'
data_cleaned = data.withColumn(
    'Related Video IDs',
    when(col('Related Video IDs') == '', None).otherwise(col('Related Video IDs'))
)

In [0]:
data_cleaned[data_cleaned['Related Video IDs']==''].count()

0

In [0]:
data=data_cleaned

In [0]:
data.count()

4066

In [0]:
data.dropna()

DataFrame[Video ID: string, Video Uploader: string, Interval between YouTube Establishment and Video Upload: double, Video Category: string, Video Length: int, Number of Views: int, Rating on the Video: double, Number of Ratings: int, Number of Comments: int, Related Video IDs: string]

In [0]:
data.count()

4066

In [0]:
data = data.filter(col('Related Video IDs').isNotNull())

In [0]:
data.count()

3239

In [0]:
data.toPandas()

Video ID  ...                                  Related Video IDs
0     QuRYeRnAuXM  ...  nRcovJn9xHg,3TYqkBJ9YRk,rSJ8QZWBegU,0TZqX5MbXM...
1     3TYqkBJ9YRk  ...  gFa1YMEJFag,UEvVksP91kg,rSJ8QZWBegU,nRcovJn9xH...
2     rSJ8QZWBegU  ...  gFa1YMEJFag,UEvVksP91kg,3TYqkBJ9YRk,nRcovJn9xH...
3     nRcovJn9xHg  ...  gFa1YMEJFag,UEvVksP91kg,3TYqkBJ9YRk,ZTopArY7Nb...
4     UEvVksP91kg  ...  QuRYeRnAuXM,3TYqkBJ9YRk,0TZqX5MbXMA,rSJ8QZWBeg...
...           ...  ...                                                ...
3234  S95602a7cFE  ...  bLAP45F4UCw,URIaUbRjIrU,x2TUkfeO-gM,Ydm5IedLYS...
3235  esCvu46qDaA  ...  vOskZNJJII8,q3qdBVDZrmE,mLDLe024T_I,bhLbFGVduT...
3236  GSsVZcKHues  ...  vOskZNJJII8,_X5nHLOiAVo,cNION6wGuso,5-reBn0gUk...
3237  foKRqJGcbPQ  ...  _X5nHLOiAVo,5-reBn0gUkg,e8bEzU2Tx7c,e4yx1s-l6f...
3238  -CYhSNHbeC8  ...  EOj-iWkcJPU,pg3j4IBMRZE,2GHiAEeFQs0,e4yx1s-l6f...

[3239 rows x 10 columns]

In [0]:
# Define the directory path to save the CSV files in DBFS
output_path = '/dbfs/Workspace/Users/d-user11@heu.ai/output.csv'

# Export the DataFrame to a CSV file
data.write.csv(output_path, header=True,mode='overwrite')

In [0]:
# List files in a directory
dbutils.fs.ls("/dbfs/Workspace/Users/d-user11@heu.ai/")

[FileInfo(path='dbfs:/dbfs/Workspace/Users/d-user11@heu.ai/output.csv/', name='output.csv/', size=0, modificationTime=1724989443000)]

In [0]:
# Read a CSV file from DBFS
dfo = spark.read.csv("/dbfs/Workspace/Users/d-user11@heu.ai/output.csv", header=True, inferSchema=True)
dfo.toPandas()



Video ID  ...                                  Related Video IDs
0     QuRYeRnAuXM  ...  nRcovJn9xHg,3TYqkBJ9YRk,rSJ8QZWBegU,0TZqX5MbXM...
1     3TYqkBJ9YRk  ...  gFa1YMEJFag,UEvVksP91kg,rSJ8QZWBegU,nRcovJn9xH...
2     rSJ8QZWBegU  ...  gFa1YMEJFag,UEvVksP91kg,3TYqkBJ9YRk,nRcovJn9xH...
3     nRcovJn9xHg  ...  gFa1YMEJFag,UEvVksP91kg,3TYqkBJ9YRk,ZTopArY7Nb...
4     UEvVksP91kg  ...  QuRYeRnAuXM,3TYqkBJ9YRk,0TZqX5MbXMA,rSJ8QZWBeg...
...           ...  ...                                                ...
3234  S95602a7cFE  ...  bLAP45F4UCw,URIaUbRjIrU,x2TUkfeO-gM,Ydm5IedLYS...
3235  esCvu46qDaA  ...  vOskZNJJII8,q3qdBVDZrmE,mLDLe024T_I,bhLbFGVduT...
3236  GSsVZcKHues  ...  vOskZNJJII8,_X5nHLOiAVo,cNION6wGuso,5-reBn0gUk...
3237  foKRqJGcbPQ  ...  _X5nHLOiAVo,5-reBn0gUkg,e8bEzU2Tx7c,e4yx1s-l6f...
3238  -CYhSNHbeC8  ...  EOj-iWkcJPU,pg3j4IBMRZE,2GHiAEeFQs0,e4yx1s-l6f...

[3239 rows x 10 columns]

In [0]:
# Analysis and Insights
# 1. Top Video Categories
# Objective: Find the top video categories with the maximum number of videos uploaded.



In [0]:
# Group by 'Category' and count the number of videos in each category
category_data = data.groupBy('Video Category').count()

# Display the result
category_data.toPandas()

Video Category  count
0               Education     43
1           Entertainment    715
2         Travel & Events     60
3    Science & Technology     74
4                  Sports    205
5           Howto & Style    111
6   Nonprofits & Activism     34
7        Film & Animation    204
8          People & Blogs    306
9         News & Politics    268
10         Pets & Animals     70
11       Autos & Vehicles     62
12                  Music    741
13                 Comedy    346

In [0]:
from pyspark.sql import functions as F

In [0]:
# Group by 'Video Category' and count the number of videos in each category
category_data = data.groupBy('Video Category').count()

# Sort the result by 'count' in descending order
sorted_category_data = category_data.orderBy(F.desc('count'))

# Display the result
sorted_category_data.show()

+--------------------+-----+
|      Video Category|count|
+--------------------+-----+
|               Music|  741|
|       Entertainment|  715|
|              Comedy|  346|
|      People & Blogs|  306|
|     News & Politics|  268|
|              Sports|  205|
|    Film & Animation|  204|
|       Howto & Style|  111|
|Science & Technology|   74|
|      Pets & Animals|   70|
|    Autos & Vehicles|   62|
|     Travel & Events|   60|
|           Education|   43|
|Nonprofits & Acti...|   34|
+--------------------+-----+



In [0]:
# Convert to Pandas DataFrame
sorted_category_df = sorted_category_data.toPandas()
print(sorted_category_df)

           Video Category  count
0                   Music    741
1           Entertainment    715
2                  Comedy    346
3          People & Blogs    306
4         News & Politics    268
5                  Sports    205
6        Film & Animation    204
7           Howto & Style    111
8    Science & Technology     74
9          Pets & Animals     70
10       Autos & Vehicles     62
11        Travel & Events     60
12              Education     43
13  Nonprofits & Activism     34


In [0]:
# Sort the result by 'count' in descending order
sorted_category_data = category_data.orderBy(F.desc('count')).limit(10)

# Display the result
sorted_category_data.show()

+--------------------+-----+
|      Video Category|count|
+--------------------+-----+
|               Music|  741|
|       Entertainment|  715|
|              Comedy|  346|
|      People & Blogs|  306|
|     News & Politics|  268|
|              Sports|  205|
|    Film & Animation|  204|
|       Howto & Style|  111|
|Science & Technology|   74|
|      Pets & Animals|   70|
+--------------------+-----+



In [0]:
# 2. Top Rated Videos
# Objective: Identify the top-rated videos on YouTube.

In [0]:
df=data.select('Video ID','Rating on the Video')

In [0]:
df.toPandas()

Video ID  Rating on the Video
0     QuRYeRnAuXM                 4.96
1     3TYqkBJ9YRk                 5.00
2     rSJ8QZWBegU                 4.31
3     nRcovJn9xHg                 2.23
4     UEvVksP91kg                 2.67
...           ...                  ...
3234  S95602a7cFE                 4.51
3235  esCvu46qDaA                 4.84
3236  GSsVZcKHues                 4.86
3237  foKRqJGcbPQ                 4.45
3238  -CYhSNHbeC8                 4.30

[3239 rows x 2 columns]

In [0]:
sorted_rating_data=df.orderBy('Rating on the Video',ascending=False)

In [0]:
sorted_rating_data.show()

+-----------+-------------------+
|   Video ID|Rating on the Video|
+-----------+-------------------+
|IU78CciLDh8|                5.0|
|muaTrM7Ouxw|                5.0|
|-zDIXUSL174|                5.0|
|Y_hAXbgxXp8|                5.0|
|YZev1imoxX8|                5.0|
|p3KqyCDaH28|                5.0|
|9l2qbaOMbcU|                5.0|
|2hZx3yBoNw4|                5.0|
|osqnkdc349s|                5.0|
|Cj_S_rut3LQ|                5.0|
|l6-J82_3utA|                5.0|
|zokUPp_nj_c|                5.0|
|AkYFKuGJEsE|                5.0|
|L3mR8syHNIg|                5.0|
|Zs4H9Itl40c|                5.0|
|ZEDYzwdqHrU|                5.0|
|bIP1V1u2q-E|                5.0|
|3TYqkBJ9YRk|                5.0|
|5vLbA7n8EG0|                5.0|
|4z31fXh-UEY|                5.0|
+-----------+-------------------+
only showing top 20 rows



In [0]:
sorted_rating_data.limit(10).show()

+-----------+-------------------+
|   Video ID|Rating on the Video|
+-----------+-------------------+
|-zDIXUSL174|                5.0|
|YZev1imoxX8|                5.0|
|3TYqkBJ9YRk|                5.0|
|L3mR8syHNIg|                5.0|
|Y_hAXbgxXp8|                5.0|
|9l2qbaOMbcU|                5.0|
|2hZx3yBoNw4|                5.0|
|Cj_S_rut3LQ|                5.0|
|osqnkdc349s|                5.0|
|ZEDYzwdqHrU|                5.0|
+-----------+-------------------+



In [0]:
# 3. Evolution of Uploaded Videos Over Time
# Objective: Analyze how the number of videos uploaded has changed over time.

In [0]:
# Group by 'Upload Interval' and count the number of videos uploaded
upload_trend = data.groupBy('Interval between YouTube Establishment and Video Upload').count()

In [0]:
display(upload_trend)

Interval between YouTube Establishment and Video Upload count 1051.0 5 299.0 1 692.0 2 934.0 4 769.0 2 558.0 3 496.0 1 782.0 6 576.0 1 720.0 3 810.0 1 735.0 2 994.0 6 486.0 4 878.0 7 1095.0 9 702.0 2 818.0 1 973.0 8 524.0 3 857.0 6 389.0 1 390.0 3 757.0 5 840.0 1 729.0 2 594.0 3 889.0 4 1135.0 198 401.0 2 925.0 4 803.0 4 1130.0 37 984.0 4 902.0 1 699.0 2 1131.0 77 1084.0 13 611.0 2 663.0 2 724.0 1 802.0 1 921.0 4 451.0 2 827.0 4 1047.0 6 774.0 2 936.0 7 879.0 3 1020.0 3 521.0 1 858.0 4 438.0 1 1012.0 5 928.0 1 681.0 2 643.0 1 567.0 2 1063.0 8 997.0 4 485.0 2 456.0 1 625.0 4 685.0 2 588.0 2 775.0 2 331.0 1 800.0 1 741.0 1 1091.0 15 1057.0 4 763.0 5 632.0 1 1081.0 9 387.0 1 627.0 2 1060.0 5 831.0 6 430.0 1 439.0 2 533.0 1 645.0 3 659.0 2 853.0 2 1015.0 2 442.0 1 509.0 3 905.0 4 672.0 1 1123.0 21 883.0 2 875.0 2 1026.0 4 358.0 1 449.0 1 403.0 1 937.0 9 908.0 3 286.0 1 959.0 5 772.0 6 946.0 3 795.0 9 914.0 2 542.0 1 733.0 1 436.0 1 443.0 1 1092.0 12 1074.0 8 1033.0 12 584.0 2 924.0 1 916.0 4 478.0 1 563.0 2 704.0 2 687.0 2 1126.0 30 838.0 5 705.0 5 321.0 1 1024.0 11 745.0 1 986.0 3 606.0 3 491.0 1 1112.0 18 995.0 1 602.0 4 730.0 1 445.0 1 728.0 7 920.0 5 812.0 1 762.0 1 794.0 4 412.0 2 737.0 3 380.0 1 974.0 3 490.0 3 1006.0 3 538.0 4 799.0 5 215.0 1 970.0 2 465.0 1 767.0 5 494.0 1 514.0 1 942.0 4 981.0 6 1028.0 4 642.0 4 396.0 1 641.0 2 980.0 3 906.0 4 945.0 5 684.0 2 721.0 4 405.0 2 476.0 2 842.0 2 577.0 2 874.0 3 529.0 2 578.0 1 1042.0 5 780.0 4 591.0 1 621.0 2 1008.0 6 783.0 2 440.0 1 620.0 2 868.0 2 983.0 4 482.0 1 781.0 2 393.0 1 511.0 4 917.0 2 426.0 1 765.0 3 740.0 2 993.0 4 373.0 1 535.0 2 829.0 1 929.0 1 998.0 8 634.0 3 817.0 2 328.0 1 377.0 1 824.0 2 603.0 6 1073.0 6 312.0 1 562.0 3 777.0 4 448.0 1 547.0 2 855.0 4 555.0 1 300.0 1 969.0 3 1034.0 1 742.0 1 1035.0 4 843.0 3 481.0 2 734.0 2 551.0 1 888.0 2 1072.0 5 709.0 2 913.0 1 919.0 1 987.0 6 1030.0 8 911.0 4 884.0 2 833.0 3 700.0 1 1004.0 4 844.0 4 779.0 3 364.0 1 923.0 3 922.0 5 1058.0 9 1003.0 5 894.0 1 949.0 1 334.0 1 1070.0 3 927.0 2 460.0 1 960.0 6 1075.0 13 599.0 1 992.0 2 293.0 1 859.0 7 1001.0 5 696.0 2 1071.0 9 1124.0 23 792.0 1 284.0 1 337.0 1 951.0 2 1061.0 7 1129.0 52 464.0 2 1007.0 4 581.0 1 453.0 1 985.0 4 468.0 2 479.0 2 788.0 2 1041.0 1 933.0 2 881.0 6 961.0 7 798.0 2 649.0 1 978.0 5 678.0 2 1048.0 8 931.0 2 813.0 2 747.0 4 948.0 4 935.0 4 845.0 3 862.0 3 873.0 2 712.0 2 1054.0 10 330.0 1 523.0 1 480.0 1 435.0 3 1116.0 17 370.0 1 585.0 2 759.0 5 652.0 2 789.0 3 516.0 1 972.0 4 432.0 1 1021.0 8 644.0 1 561.0 1 787.0 2 746.0 1 694.0 3 676.0 2 854.0 3 527.0 2 285.0 1 624.0 1 386.0 1 877.0 6 1101.0 15 976.0 2 610.0 2 835.0 4 977.0 2 918.0 6 846.0 1 559.0 1 825.0 3 1013.0 4 618.0 1 926.0 5 785.0 2 820.0 1 1011.0 7 493.0 2 1078.0 7 719.0 5 866.0 3 1025.0 3 764.0 5 714.0 1 416.0 1 1010.0 4 1109.0 13 361.0 2 968.0 3 1076.0 5 943.0 2 572.0 1 661.0 1 541.0 2 675.0 1 863.0 9 532.0 1 786.0 2 717.0 2 310.0 1 630.0 1 467.0 3 751.0 4 1014.0 5 658.0 2 612.0 1 955.0 1 404.0 3 1059.0 7 975.0 12 815.0 4 979.0 2 909.0 2 473.0 1 534.0 2 600.0 2 1045.0 10 690.0 1 1125.0 18 821.0 3 941.0 3 580.0 2 637.0 2 711.0 2 1114.0 16 332.0 1 904.0 5 537.0 1 646.0 2 732.0 1 898.0 3 891.0 3 695.0 2 1067.0 12 1055.0 8 619.0 1 391.0 1 865.0 3 697.0 3 668.0 1 832.0 3 1117.0 14 1108.0 16 1064.0 4 999.0 4 411.0 1 1136.0 30 890.0 2 869.0 3 640.0 1 498.0 1 415.0 1 613.0 3 1019.0 5 807.0 5 900.0 2 836.0 1 903.0 5 575.0 3 856.0 6 706.0 8 1062.0 9 837.0 2 654.0 1 648.0 3 1127.0 32 628.0 1 1110.0 7 930.0 6 776.0 4 1053.0 7 703.0 2 790.0 1 841.0 2 1043.0 3 553.0 1 1105.0 17 461.0 3 847.0 5 739.0 2 870.0 7 1040.0 8 849.0 7 966.0 1 504.0 1 1009.0 5 953.0 6 1106.0 18 1089.0 4 1128.0 29 1031.0 8 885.0 3 796.0 4 718.0 3 1016.0 7 770.0 7 497.0 2 489.0 1 760.0 2 744.0 4 851.0 5 639.0 2 488.0 1 778.0 1 876.0 3 615.0 2 338.0 1 962.0 6 1056.0 7 1027.0 3 1018.0 4 826.0 1 982.0 4 899.0 2 1097.0 9 932.0 2 1093.0 14 1023.0 3 895.0 1 1104.0 10 1046.0 5 1050.0 6 872.0 4 289.0 1 896.0 3 502.0 1 609.0 1 682.0 1 1094.0 

In [0]:
# Sort the result by 'Upload Interval' in ascending order to see the trend over time
upload_trend = upload_trend.orderBy(asc('Interval between YouTube Establishment and Video Upload'))

# Display the result
upload_trend.toPandas()

Interval between YouTube Establishment and Video Upload  count
0                                                215.0            1
1                                                265.0            1
2                                                284.0            1
3                                                285.0            1
4                                                286.0            1
..                                                 ...          ...
660                                             1132.0           59
661                                             1133.0           98
662                                             1134.0          161
663                                             1135.0          198
664                                             1136.0           30

[665 rows x 2 columns]

In [0]:
# Sort the result by 'Count' in descending order to see the trend over time
upload_trend = upload_trend.orderBy(desc('count'))

# Display the result
upload_trend.toPandas()

Interval between YouTube Establishment and Video Upload  count
0                                               1135.0          198
1                                               1134.0          161
2                                               1133.0           98
3                                               1131.0           77
4                                               1132.0           59
..                                                 ...          ...
660                                              398.0            1
661                                              382.0            1
662                                              512.0            1
663                                              814.0            1
664                                              505.0            1

[665 rows x 2 columns]

In [0]:
# 4. Correlation between Establishment Interval and Video Popularity
# Objective: Investigate if there is a correlation between the interval between YouTube establishment and video upload date and video popularity.

In [0]:
# Select relevant columns for correlation analysis
columns_for_corr = [
    'Interval between YouTube Establishment and Video Upload',
    'Number of Views',
    'Rating on the Video',
    'Number of Ratings',
    'Number of Comments'
]


In [0]:
# Filter the data to include only the relevant columns
filtered_data = data.select(columns_for_corr)

In [0]:
# Calculate the correlation between 'Interval between YouTube Establishment and Video Upload' and other metrics
correlation_views = filtered_data.stat.corr('Interval between YouTube Establishment and Video Upload', 'Number of Views')
correlation_ratings = filtered_data.stat.corr('Interval between YouTube Establishment and Video Upload', 'Rating on the Video')
correlation_num_ratings = filtered_data.stat.corr('Interval between YouTube Establishment and Video Upload', 'Number of Ratings')
correlation_comments = filtered_data.stat.corr('Interval between YouTube Establishment and Video Upload', 'Number of Comments')


In [0]:
# Display the correlation results
print(f"Correlation between Interval and Number of Views: {correlation_views}")
print(f"Correlation between Interval and Rating on the Video: {correlation_ratings}")
print(f"Correlation between Interval and Number of Ratings: {correlation_num_ratings}")
print(f"Correlation between Interval and Number of Comments: {correlation_comments}")

Correlation between Interval and Number of Views: -0.15727255139253954
Correlation between Interval and Rating on the Video: -0.22748673987843424
Correlation between Interval and Number of Ratings: -0.1184893103517689
Correlation between Interval and Number of Comments: -0.05905373629326027


In [0]:
# Correlation Coefficients:
# The correlation coefficient ranges from -1 to 1.
# A value closer to 1 indicates a strong positive correlation.
# A value closer to -1 indicates a strong negative correlation.
# A value near 0 indicates no correlation.

In [0]:
df=data
display(df)

Video ID Video Uploader Interval between YouTube Establishment and Video Upload Video Category Video Length Number of Views Rating on the Video Number of Ratings Number of Comments Related Video IDs QuRYeRnAuXM EvilSquirrelPictures 1135.0 Pets & Animals 252 1075 4.96 46 86 nRcovJn9xHg,3TYqkBJ9YRk,rSJ8QZWBegU,0TZqX5MbXMA,UEvVksP91kg,ZTopArY7Nbg,0RViGi2Rne8,HT_QlOJbDpg,YZev1imoxX8,8qQrrfUTmh0,zQ83d_D2MGs,u6_DQQjLsAw,73Wz9CQFDtE 3TYqkBJ9YRk hggh22 1135.0 Comedy 169 228 5.0 5 3 gFa1YMEJFag,UEvVksP91kg,rSJ8QZWBegU,nRcovJn9xHg,sVkuOk4jmCo,ZTopArY7Nbg,HT_QlOJbDpg,0RViGi2Rne8,ShhClb6J-NA,g9e1alirMhc,YZev1imoxX8,I4yKEK9o8gA,zQ83d_D2MGs rSJ8QZWBegU TimeGem 1135.0 Entertainment 95 356 4.31 13 1 gFa1YMEJFag,UEvVksP91kg,3TYqkBJ9YRk,nRcovJn9xHg,sVkuOk4jmCo,ZTopArY7Nbg,gBcu22Vv1nY,HT_QlOJbDpg,0RViGi2Rne8,ShhClb6J-NA,g9e1alirMhc,YZev1imoxX8,I4yKEK9o8gA nRcovJn9xHg wooochacha 1135.0 Entertainment 118 1115 2.23 57 73 gFa1YMEJFag,UEvVksP91kg,3TYqkBJ9YRk,ZTopArY7Nbg,gBcu22Vv1nY,HT_QlOJbDpg,0RViGi2Rne8,ShhClb6J-NA,g9e1alirMhc,YZev1imoxX8,I4yKEK9o8gA,zQ83d_D2MGs,1GKaVzNDbuI UEvVksP91kg johnx113 1135.0 Entertainment 83 281 2.67 9 16 QuRYeRnAuXM,3TYqkBJ9YRk,0TZqX5MbXMA,rSJ8QZWBegU,nRcovJn9xHg,sVkuOk4jmCo,ZTopArY7Nbg,HT_QlOJbDpg,0RViGi2Rne8,g9e1alirMhc,YZev1imoxX8,I4yKEK9o8gA,zQ83d_D2MGs sVkuOk4jmCo marcosoycadiz 1135.0 People & Blogs 49 1196 3.67 6 5 sLrWjhvCoW8,dergWtU1tnE,Cs3TbaYxg_A,OOHsD-akNw0,9Vajm_u9TsI,ZW62z2-QfpA,4ki_fVDDlzs,WJ2WTPtijSc,8TknA5BqRBc,M2fcueuny7s,8Wd6y3Pb2yA,0aKz7qdtMj0,x50W-TW6yGg ZTopArY7Nbg TroyChannel 1136.0 Entertainment 145 11 0.0 0 0 pQPhV1mzh-g,NeIGddkjxJI,8-vZvDjh_3g,N6RuQAW1ALc,Dc_MIs3NzIQ,LsSendGJARs,MHADThckgkE,OTJGrqVOubA,BjU-c_aBXtc,dT1Hmv_2Qg8,apqOIWiKaXc,vX0vqQuXI9g,Gb7ztQ-baqo 0RViGi2Rne8 OmnipotentSI 1135.0 Entertainment 9 490 2.31 26 15 nRcovJn9xHg,0TZqX5MbXMA,UEvVksP91kg,gFa1YMEJFag,QuRYeRnAuXM,3TYqkBJ9YRk,HT_QlOJbDpg,ZTopArY7Nbg,g9e1alirMhc,YZev1imoxX8,I4yKEK9o8gA,zQ83d_D2MGs,1GKaVzNDbuI HT_QlOJbDpg dumbasstheredneck 1095.0 Comedy 14 1349 2.09 22 13 jVxz9wKEa3A,mUoRI-VnV6w,bGRB0Pwx_iM,B09qqpGr4Xo,6Xdg_elOGaY,8-7axRRXpfE,VO_mUdKmyds,1vGH08qoclk,eP94rcWKMNM,jFGu4xEvWUc,e7SnPCWPFxE,G_my4iaIYIM,e9y0_BgZU7g ShhClb6J-NA thecrashguy 1136.0 Entertainment 61 29 0.0 0 0 6DK-CJh6hTY,SArJyLS6T_Y,boRch04lh0I,yop2Ipym-ls,Ydnc_c4Afj0,HFaCubSrqdQ,tpUcCvJ9cio,8MrfxlBkHMQ,_CNGEzIuf_I,bKOzgNvNgTE,JJtHjzlBigU,fGkPWRrOTXA,oBqH_5mPxsc g9e1alirMhc iamdanielisaac 541.0 Comedy 152 483053 4.65 2689 2932 1GKaVzNDbuI,Bd61LnxqSng,97cWs8tW8mY,I4yKEK9o8gA,IBqQWAjBgmE,myQpL8_M980,WWqed9u6rr4,-mQH9DloKD8,2l6vwAIAqNU,E3XaD3Yu3qA,pFUYi7dp1WU,Dto7-3aOt8w,hiSmlmXp-aU YZev1imoxX8 threefirstnames 1135.0 Entertainment 253 63 5.0 3 2 -UvVtpmh4EQ,BzwpvskqHa4,OJtAoLrGA8Q,q5QOvQ8ZYUQ,MFmMssHR0Rc,vDuIB8Gv9GQ,3kITDVTeo-c,Dt5X1_3S_kM,P2OguaWyfzQ,vOAYUoiPkzA,_6ruNbrssO4,sSUu4ROj3FQ,n5Ngq0mKKzA I4yKEK9o8gA djlogitek 964.0 News & Politics 173 106929 4.39 1010 1484 1GKaVzNDbuI,qCUYgddlvRM,J0Qu6eyyr4c,8n-nT-luFIw,q8XToX7aSdg,dzUNvEfYDEQ,WWqed9u6rr4,2l6vwAIAqNU,VWYX-LiQggc,gMuxyRbNLFM,IBqQWAjBgmE,JZekosYOmXc,DomumdGQSg8 1GKaVzNDbuI fatvids 690.0 Comedy 176 2464486 4.5 13342 11997 g9e1alirMhc,UrNqx1p95qs,sEJLOmVOpcU,WGV4u6GhGhw,Dto7-3aOt8w,I4yKEK9o8gA,p9CypIsNSvM,qJXYN3wFhgo,Vqiw-Kqtlr0,bnuaPr4hlCU,CKjha-rohzc,hSlo0T0CNI4,_i6OD_y_-AI yuZhwV24PmM weneedhelp 1082.0 News & Politics 213 46183 4.71 280 247 xq8aopATYyw,g9e1alirMhc,I4yKEK9o8gA,HuTqgqhxVMc,QoMCoMMgeO0,6h3G-lMZxjo,b4LuFQJmS1Y,7ZVpPGxuafA,bfZ_gXCHaMw,1GKaVzNDbuI,9Fr1dm2Qdls,WWqed9u6rr4,L3gQfz8GC0o zQ83d_D2MGs dumbasstheredneck 1095.0 Comedy 14 1550 1.57 14 4 cdbp6rCVzRs,gAHZ7DRyIgY,mUoRI-VnV6w,jFGu4xEvWUc,TEPH9ScDy1E,AK9_-sLF5M0,6Xdg_elOGaY,p4NVl4W6FHM,mCLw4iGZ7Ms,bGRB0Pwx_iM,ifTbWQW0w64,tPi04TrYskw,n00wAO4hg-U DomumdGQSg8 imgrown18 910.0 Comedy 224 392908 4.8 1261 829 eOIFF_5ORGo,n7rlp3SLtus,u_9vYy-TCCk,kpq0zL-oW4M,J5z4Vs26-TI,b-iTzU_ZD4k,CvCqT9hkZiA,s5CqcdpwEq8,pvVo1290j1w,6g0XGKuC-ek,7TXjtbl2y3U,hpsra8ojBHQ,pqhlG9qYsR8 pFUYi7dp1WU StanleyJenkins 1106.0 Comedy 200 110272 4.07 1011 482 ue5lVJuNlzQ,AkjUO

In [0]:
# Create the "Video Popularity" column by summing the specified columns
# If you need to apply weights, you can multiply each column by its respective weight before summing
df = df.withColumn(
    'Video Popularity',
    F.col('Number of Views') + F.col('Rating on the Video') + F.col('Number of Ratings') + F.col('Number of Comments')
)

display(df)

Video ID Video Uploader Interval between YouTube Establishment and Video Upload Video Category Video Length Number of Views Rating on the Video Number of Ratings Number of Comments Related Video IDs Video Popularity QuRYeRnAuXM EvilSquirrelPictures 1135.0 Pets & Animals 252 1075 4.96 46 86 nRcovJn9xHg,3TYqkBJ9YRk,rSJ8QZWBegU,0TZqX5MbXMA,UEvVksP91kg,ZTopArY7Nbg,0RViGi2Rne8,HT_QlOJbDpg,YZev1imoxX8,8qQrrfUTmh0,zQ83d_D2MGs,u6_DQQjLsAw,73Wz9CQFDtE 1211.96 3TYqkBJ9YRk hggh22 1135.0 Comedy 169 228 5.0 5 3 gFa1YMEJFag,UEvVksP91kg,rSJ8QZWBegU,nRcovJn9xHg,sVkuOk4jmCo,ZTopArY7Nbg,HT_QlOJbDpg,0RViGi2Rne8,ShhClb6J-NA,g9e1alirMhc,YZev1imoxX8,I4yKEK9o8gA,zQ83d_D2MGs 241.0 rSJ8QZWBegU TimeGem 1135.0 Entertainment 95 356 4.31 13 1 gFa1YMEJFag,UEvVksP91kg,3TYqkBJ9YRk,nRcovJn9xHg,sVkuOk4jmCo,ZTopArY7Nbg,gBcu22Vv1nY,HT_QlOJbDpg,0RViGi2Rne8,ShhClb6J-NA,g9e1alirMhc,YZev1imoxX8,I4yKEK9o8gA 374.31 nRcovJn9xHg wooochacha 1135.0 Entertainment 118 1115 2.23 57 73 gFa1YMEJFag,UEvVksP91kg,3TYqkBJ9YRk,ZTopArY7Nbg,gBcu22Vv1nY,HT_QlOJbDpg,0RViGi2Rne8,ShhClb6J-NA,g9e1alirMhc,YZev1imoxX8,I4yKEK9o8gA,zQ83d_D2MGs,1GKaVzNDbuI 1247.23 UEvVksP91kg johnx113 1135.0 Entertainment 83 281 2.67 9 16 QuRYeRnAuXM,3TYqkBJ9YRk,0TZqX5MbXMA,rSJ8QZWBegU,nRcovJn9xHg,sVkuOk4jmCo,ZTopArY7Nbg,HT_QlOJbDpg,0RViGi2Rne8,g9e1alirMhc,YZev1imoxX8,I4yKEK9o8gA,zQ83d_D2MGs 308.67 sVkuOk4jmCo marcosoycadiz 1135.0 People & Blogs 49 1196 3.67 6 5 sLrWjhvCoW8,dergWtU1tnE,Cs3TbaYxg_A,OOHsD-akNw0,9Vajm_u9TsI,ZW62z2-QfpA,4ki_fVDDlzs,WJ2WTPtijSc,8TknA5BqRBc,M2fcueuny7s,8Wd6y3Pb2yA,0aKz7qdtMj0,x50W-TW6yGg 1210.67 ZTopArY7Nbg TroyChannel 1136.0 Entertainment 145 11 0.0 0 0 pQPhV1mzh-g,NeIGddkjxJI,8-vZvDjh_3g,N6RuQAW1ALc,Dc_MIs3NzIQ,LsSendGJARs,MHADThckgkE,OTJGrqVOubA,BjU-c_aBXtc,dT1Hmv_2Qg8,apqOIWiKaXc,vX0vqQuXI9g,Gb7ztQ-baqo 11.0 0RViGi2Rne8 OmnipotentSI 1135.0 Entertainment 9 490 2.31 26 15 nRcovJn9xHg,0TZqX5MbXMA,UEvVksP91kg,gFa1YMEJFag,QuRYeRnAuXM,3TYqkBJ9YRk,HT_QlOJbDpg,ZTopArY7Nbg,g9e1alirMhc,YZev1imoxX8,I4yKEK9o8gA,zQ83d_D2MGs,1GKaVzNDbuI 533.31 HT_QlOJbDpg dumbasstheredneck 1095.0 Comedy 14 1349 2.09 22 13 jVxz9wKEa3A,mUoRI-VnV6w,bGRB0Pwx_iM,B09qqpGr4Xo,6Xdg_elOGaY,8-7axRRXpfE,VO_mUdKmyds,1vGH08qoclk,eP94rcWKMNM,jFGu4xEvWUc,e7SnPCWPFxE,G_my4iaIYIM,e9y0_BgZU7g 1386.09 ShhClb6J-NA thecrashguy 1136.0 Entertainment 61 29 0.0 0 0 6DK-CJh6hTY,SArJyLS6T_Y,boRch04lh0I,yop2Ipym-ls,Ydnc_c4Afj0,HFaCubSrqdQ,tpUcCvJ9cio,8MrfxlBkHMQ,_CNGEzIuf_I,bKOzgNvNgTE,JJtHjzlBigU,fGkPWRrOTXA,oBqH_5mPxsc 29.0 g9e1alirMhc iamdanielisaac 541.0 Comedy 152 483053 4.65 2689 2932 1GKaVzNDbuI,Bd61LnxqSng,97cWs8tW8mY,I4yKEK9o8gA,IBqQWAjBgmE,myQpL8_M980,WWqed9u6rr4,-mQH9DloKD8,2l6vwAIAqNU,E3XaD3Yu3qA,pFUYi7dp1WU,Dto7-3aOt8w,hiSmlmXp-aU 488678.65 YZev1imoxX8 threefirstnames 1135.0 Entertainment 253 63 5.0 3 2 -UvVtpmh4EQ,BzwpvskqHa4,OJtAoLrGA8Q,q5QOvQ8ZYUQ,MFmMssHR0Rc,vDuIB8Gv9GQ,3kITDVTeo-c,Dt5X1_3S_kM,P2OguaWyfzQ,vOAYUoiPkzA,_6ruNbrssO4,sSUu4ROj3FQ,n5Ngq0mKKzA 73.0 I4yKEK9o8gA djlogitek 964.0 News & Politics 173 106929 4.39 1010 1484 1GKaVzNDbuI,qCUYgddlvRM,J0Qu6eyyr4c,8n-nT-luFIw,q8XToX7aSdg,dzUNvEfYDEQ,WWqed9u6rr4,2l6vwAIAqNU,VWYX-LiQggc,gMuxyRbNLFM,IBqQWAjBgmE,JZekosYOmXc,DomumdGQSg8 109427.39 1GKaVzNDbuI fatvids 690.0 Comedy 176 2464486 4.5 13342 11997 g9e1alirMhc,UrNqx1p95qs,sEJLOmVOpcU,WGV4u6GhGhw,Dto7-3aOt8w,I4yKEK9o8gA,p9CypIsNSvM,qJXYN3wFhgo,Vqiw-Kqtlr0,bnuaPr4hlCU,CKjha-rohzc,hSlo0T0CNI4,_i6OD_y_-AI 2489829.5 yuZhwV24PmM weneedhelp 1082.0 News & Politics 213 46183 4.71 280 247 xq8aopATYyw,g9e1alirMhc,I4yKEK9o8gA,HuTqgqhxVMc,QoMCoMMgeO0,6h3G-lMZxjo,b4LuFQJmS1Y,7ZVpPGxuafA,bfZ_gXCHaMw,1GKaVzNDbuI,9Fr1dm2Qdls,WWqed9u6rr4,L3gQfz8GC0o 46714.71 zQ83d_D2MGs dumbasstheredneck 1095.0 Comedy 14 1550 1.57 14 4 cdbp6rCVzRs,gAHZ7DRyIgY,mUoRI-VnV6w,jFGu4xEvWUc,TEPH9ScDy1E,AK9_-sLF5M0,6Xdg_elOGaY,p4NVl4W6FHM,mCLw4iGZ7Ms,bGRB0Pwx_iM,ifTbWQW0w64,tPi04TrYskw,n00wAO4hg-U 1569.57 DomumdGQSg8 imgrown18 910.0 Comedy 224 392908 4.8 1261 829 eOIFF_5ORGo,n7rlp3SLtus,u_9vYy-TCCk,kpq0zL-oW4M,J5z4Vs26-TI,b-iTzU_ZD4k,CvCqT9hkZiA,s5CqcdpwEq8,pvVo1

In [0]:
df=df.select(['Interval between YouTube Establishment and Video Upload','Video Popularity'])

In [0]:
df.toPandas()

Interval between YouTube Establishment and Video Upload  Video Popularity
0                                                1135.0                 1211.96
1                                                1135.0                  241.00
2                                                1135.0                  374.31
3                                                1135.0                 1247.23
4                                                1135.0                  308.67
...                                                 ...                     ...
3234                                             1045.0                40083.51
3235                                              863.0               117337.84
3236                                             1024.0               489618.86
3237                                             1100.0                13189.45
3238                                              771.0               104057.30

[3239 rows x 2 columns]

In [0]:
df=df.orderBy(desc('Video Popularity'))
df.toPandas()

Interval between YouTube Establishment and Video Upload  Video Popularity
0                                                 404.0             65356625.03
1                                                 933.0             33877912.84
2                                                 807.0             27804548.88
3                                                 937.0             18617277.42
4                                                 857.0             18194029.83
...                                                 ...                     ...
3234                                             1134.0                    8.00
3235                                             1135.0                    8.00
3236                                             1135.0                    7.00
3237                                             1135.0                    5.00
3238                                             1135.0                    0.00

[3239 rows x 2 columns]

In [0]:
# Normalize the Video Popularity Column using Min-Max Normalization

In [0]:
# Calculate the minimum and maximum values of the column
min_value = df.agg(F.min('Video Popularity')).collect()[0][0]
max_value = df.agg(F.max('Video Popularity')).collect()[0][0]

print(min_value,max_value)

0.0 65356625.03


In [0]:
# Normalized Value= (Original Value−Min Value) / (Max Value−Min Value)


In [0]:
# Normalize the column 'Video Popularity' to the range 0-1
df = df.withColumn('Normalized Video Popularity',(F.col('Video Popularity') - min_value)/ (max_value -min_value))

In [0]:
df.show()

+-------------------------------------------------------+----------------+---------------------------+
|Interval between YouTube Establishment and Video Upload|Video Popularity|Normalized Video Popularity|
+-------------------------------------------------------+----------------+---------------------------+
|                                                  404.0|   6.535662503E7|                        1.0|
|                                                  933.0|   3.387791284E7|         0.5183546859166819|
|                                                  807.0|   2.780454888E7|         0.4254281622901604|
|                                                  937.0|   1.861727742E7|         0.2848567748327625|
|                                                  857.0|   1.819402983E7|         0.2783808041135627|
|                                                  796.0|   1.705428723E7|          0.260941981354939|
|                                                  751.0|    1.30684338E7

In [0]:
df=df.select(["Interval between YouTube Establishment and Video Upload","Normalized Video Popularity"])

In [0]:
df=df.orderBy(desc("Normalized Video Popularity"))
df.show()

+-------------------------------------------------------+---------------------------+
|Interval between YouTube Establishment and Video Upload|Normalized Video Popularity|
+-------------------------------------------------------+---------------------------+
|                                                  404.0|                        1.0|
|                                                  933.0|         0.5183546859166819|
|                                                  807.0|         0.4254281622901604|
|                                                  937.0|         0.2848567748327625|
|                                                  857.0|         0.2783808041135627|
|                                                  796.0|          0.260941981354939|
|                                                  751.0|        0.19995576261781156|
|                                                  848.0|        0.17003441999795685|
|                                                  215

In [0]:
df=df.orderBy(asc("Normalized Video Popularity"))
df.show()

+-------------------------------------------------------+---------------------------+
|Interval between YouTube Establishment and Video Upload|Normalized Video Popularity|
+-------------------------------------------------------+---------------------------+
|                                                 1135.0|                        0.0|
|                                                 1135.0|       7.650333837931349E-8|
|                                                 1135.0|       1.071046737310388...|
|                                                 1134.0|       1.224053414069016E-7|
|                                                 1135.0|       1.224053414069016E-7|
|                                                 1136.0|       1.683073444344896...|
|                                                 1135.0|       1.836080121103523...|
|                                                 1135.0|       1.989086797862150...|
|                                                 1136

In [0]:
# Calculate the correlation between 'Interval between YouTube Establishment and Video Upload' and 'Normalized Video Popularity'
correlation_popularity = df.stat.corr('Interval between YouTube Establishment and Video Upload', 'Normalized Video Popularity')

# Display the correlation result
print(f"Correlation between Interval and Video Popularity: {correlation_popularity}")

Correlation between Interval and Video Popularity: -0.15727575962518575


In [0]:
# 5. Video Categories with Highest Average Ratings
# Objective: Determine which video categories have the highest average ratings. Sort videos in decreasing order of their ratings.

In [0]:
df=data.select(["Video Category","Rating on the Video"])
df.show()

+----------------+-------------------+
|  Video Category|Rating on the Video|
+----------------+-------------------+
|  Pets & Animals|               4.96|
|          Comedy|                5.0|
|   Entertainment|               4.31|
|   Entertainment|               2.23|
|   Entertainment|               2.67|
|  People & Blogs|               3.67|
|   Entertainment|                0.0|
|   Entertainment|               2.31|
|          Comedy|               2.09|
|   Entertainment|                0.0|
|          Comedy|               4.65|
|   Entertainment|                5.0|
| News & Politics|               4.39|
|          Comedy|                4.5|
| News & Politics|               4.71|
|          Comedy|               1.57|
|          Comedy|                4.8|
|          Comedy|               4.07|
|Film & Animation|               4.07|
|   Entertainment|               4.43|
+----------------+-------------------+
only showing top 20 rows



In [0]:
from pyspark.sql import functions as F

# Group by 'Video Category' and calculate the average rating
category_avg_rating = data.groupBy('Video Category').agg(avg('Rating on the Video').alias('Average Rating'))

# Sort the categories by the average rating in descending order
sorted_categories = category_avg_rating.orderBy(desc('Average Rating'))

# Display the result
sorted_categories.toPandas()

Video Category  Average Rating
0                   Music        4.360256
1        Film & Animation        4.317843
2        Autos & Vehicles        4.000645
3          Pets & Animals        3.931000
4                  Sports        3.910976
5           Entertainment        3.894280
6         News & Politics        3.841567
7          People & Blogs        3.829314
8                  Comedy        3.747225
9         Travel & Events        3.682333
10          Howto & Style        3.640901
11              Education        3.438605
12  Nonprofits & Activism        3.334118
13   Science & Technology        3.296892

In [0]:
# 6. Video Length and Views Relationship
# Objective: Explore the relationship between video length and the number of views.

In [0]:
df = data.select("Video Length", "Number of Views")
df.show()

+------------+---------------+
|Video Length|Number of Views|
+------------+---------------+
|         252|           1075|
|         169|            228|
|          95|            356|
|         118|           1115|
|          83|            281|
|          49|           1196|
|         145|             11|
|           9|            490|
|          14|           1349|
|          61|             29|
|         152|         483053|
|         253|             63|
|         173|         106929|
|         176|        2464486|
|         213|          46183|
|          14|           1550|
|         224|         392908|
|         200|         110272|
|         294|          71966|
|         168|         653840|
+------------+---------------+
only showing top 20 rows



In [0]:
# Calculate the correlation between 'Video Length' and 'Number of Views'
correlation = data.stat.corr('Video Length', 'Number of Views')

# Display the correlation value
print(f"Correlation between Video Length and Number of Views: {correlation}")

Correlation between Video Length and Number of Views: 0.02235301619304947


In [0]:
# 7. Comments vs. Ratings
# Objective: Investigate whether videos with more comments tend to have higher ratings.

In [0]:
df=data.select(["Video ID","Number of Comments","Rating on the Video"])
df.toPandas()

Video ID  Number of Comments  Rating on the Video
0     QuRYeRnAuXM                  86                 4.96
1     3TYqkBJ9YRk                   3                 5.00
2     rSJ8QZWBegU                   1                 4.31
3     nRcovJn9xHg                  73                 2.23
4     UEvVksP91kg                  16                 2.67
...           ...                 ...                  ...
3234  S95602a7cFE                 131                 4.51
3235  esCvu46qDaA                 222                 4.84
3236  GSsVZcKHues                1764                 4.86
3237  foKRqJGcbPQ                  37                 4.45
3238  -CYhSNHbeC8                 220                 4.30

[3239 rows x 3 columns]

In [0]:
df.orderBy(desc("Number of Comments")).toPandas()

Video ID  Number of Comments  Rating on the Video
0     kHmvkRoEowc              259683                 2.42
1     EwTZ2xpQwpA              129200                 4.23
2     4DC4Rb9quKk               50036                 4.84
3     Qit3ALTelOo               39418                 4.76
4     UW_1CvDFYVg               33543                 4.11
...           ...                 ...                  ...
3234  S2w71WtHlYw                   0                 0.00
3235  HyhoLnfqq3o                   0                 3.00
3236  St1NTAvmCIE                   0                 0.00
3237  RxE8Fl3UBc8                   0                 0.00
3238  i4QdWYCoLYs                   0                 5.00

[3239 rows x 3 columns]

In [0]:
# Calculate the correlation between 'Number of Comments' and 'Rating on the Video'
correlation_comments_ratings = df.corr('Number of Comments', 'Rating on the Video')

# Display the correlation value
print(f"Correlation between Number of Comments and Rating on the Video: {correlation_comments_ratings}")

Correlation between Number of Comments and Rating on the Video: 0.01979052003424152


In [0]:
# 8. Top Video Uploaders
# Objective: Identify the top video uploaders based on the number of views or ratings.

In [0]:
# Group by 'Video Uploader' and aggregate by the sum of 'Number of Views'
top_uploaders_by_views = data.groupBy('Video Uploader').agg(sum('Number of Views').alias('Total Views'))

# Sort the uploaders in descending order of views
top_uploaders_by_views = top_uploaders_by_views.orderBy(desc('Total Views'))

# Display the top 10 uploaders by views
top_uploaders_by_views.show(10)


+---------------+-----------+
| Video Uploader|Total Views|
+---------------+-----------+
|        kaejane|   65341925|
|   ChrisBrownTV|   33754615|
|    TPainVideos|   30197909|
|       Jason275|   27721690|
|itschriscrocker|   23473833|
|      TayZonday|   20340997|
|       RKellyTV|   13038204|
|      machinima|   11437210|
|    TownIdiot25|   11007201|
|    Frozentoast|   10172172|
+---------------+-----------+
only showing top 10 rows



In [0]:
# Group by 'Video Uploader' and aggregate by the average of 'Rating on the Video'
top_uploaders_by_rating = data.groupBy('Video Uploader').agg(avg('Rating on the Video').alias('Average Rating'))

# Sort the uploaders in descending order of average rating
top_uploaders_by_rating = top_uploaders_by_rating.orderBy(desc('Average Rating'))

# Display the top 10 uploaders by average rating
top_uploaders_by_rating.show(10)


+----------------+--------------+
|  Video Uploader|Average Rating|
+----------------+--------------+
|  dulceXyear3000|           5.0|
|         ODestre|           5.0|
|      gospel1992|           5.0|
|      amazingxx3|           5.0|
|   BeeVeeStudios|           5.0|
|     ZaffireWolf|           5.0|
|tokiohotelth4832|           5.0|
|     GetAMPEDmag|           5.0|
|      SamTubeCOM|           5.0|
|         CNTV121|           5.0|
+----------------+--------------+
only showing top 10 rows



In [0]:
# 9. Average Related Videos
# Objective: Determine how many related videos, on average, are associated with each video.

In [0]:
# Step 1: Count the number of related videos for each video
# Split the 'Related Video IDs' column by a delimiter (e.g., comma, tab) and count the number of elements
df = data.withColumn('Number of Related Videos', size(split(data['Related Video IDs'], ',')))

In [0]:
df.select(["Video ID","Number of Related Videos"]).orderBy(desc('Number of Related Videos')).toPandas()

Video ID  Number of Related Videos
0     QuRYeRnAuXM                        13
1     3TYqkBJ9YRk                        13
2     rSJ8QZWBegU                        13
3     nRcovJn9xHg                        13
4     UEvVksP91kg                        13
...           ...                       ...
3234  RqBWgTXbHsk                         4
3235  U8cmRdpcePc                         4
3236  1suivhh78jE                         4
3237  9eohCbgOwIk                         4
3238  Do9XMt1Tdgs                         1

[3239 rows x 2 columns]

In [0]:
# Step 2: Calculate the average number of related videos
average_related_videos = data.agg(avg('Number of Related Videos').alias('Average Related Videos')).first()

# Display the result
average_related_videos['Average Related Videos']

12.878357517752393

In [0]:
# 11. Overall Platform Engagement
# Objective: Evaluate the overall engagement level on the platform by analyzing the total number of views, ratings, and comments.

In [0]:
# Step 1: Sum the total number of views
total_views = data.agg(sum('Number of Views').alias('Total Views')).first()

# Step 2: Sum the total number of ratings
total_ratings = data.agg(sum('Number of Ratings').alias('Total Ratings')).first()

# Step 3: Sum the total number of comments
total_comments = data.agg(sum('Number of Comments').alias('Total Comments')).first()

# Display the overall engagement metrics
overall_engagement = {
    "Total Views": total_views['Total Views'],
    "Total Ratings": total_ratings['Total Ratings'],
    "Total Comments": total_comments['Total Comments']
}

overall_engagement

{'Total Views': 784817870, 'Total Ratings': 2376096, 'Total Comments': 2160663}